In [ ]:
#!pip install Shapely

In [1]:
import numpy as np                                 # (pip install numpy)
from skimage import measure                        # (pip install scikit-image)
from shapely.geometry import Polygon, MultiPolygon # (pip install Shapely)

def create_sub_mask_annotation(sub_mask, image_id, category_id, annotation_id, is_crowd):
    # Find contours (boundary lines) around each sub-mask
    # Note: there could be multiple contours if the object
    # is partially occluded. (E.g. an elephant behind a tree)
    contours = measure.find_contours(sub_mask, 0.5, positive_orientation='low')
    
    segmentations = []
    polygons = []
    for contour in contours:
        # Flip from (row, col) representation to (x, y)
        # and subtract the padding pixel
#         print(contour)
        for i in range(len(contour)):
            row, col = contour[i]
            contour[i] = (col - 1, row - 1)

        # Make a polygon and simplify it
        poly = Polygon(contour)
#         print(poly)
        poly = poly.simplify(1.0, preserve_topology=False)
        polygons.append(poly)
        segmentation = np.array(poly.exterior.coords).ravel().tolist()
        segmentations.append(segmentation)
    
    # Combine the polygons to calculate the bounding box and area
    multi_poly = MultiPolygon(polygons)
    x, y, max_x, max_y = multi_poly.bounds
    width = max_x - x
    height = max_y - y
    bbox = (x, y, width, height)
    area = multi_poly.area

     
    annotation = {
                   
                                
                                      'segmentation': segmentations,
                                      'area': area, 
                                      'iscrowd': is_crowd,
                                      'image_id':image_id,
                                      'bbox': bbox,
                                      'category_id':category_id, 
                                      'annotation_id': annotation_id
                                  
                
                }

    return annotation

In [2]:
from PIL import Image # (pip install Pillow)

def create_sub_masks(mask_image):
    width, height = mask_image.size
    #print(mask_image.size)
    #print(width)
    #print(height)
    # Initialize a dictionary of sub-masks indexed by RGB colors
    sub_masks = {}
    for x in range(width):
        for y in range(height):
            # Get the RGB values of the pixel
            #pixel = mask_image.getpixel((x,y))[:3]
            pixel = mask_image.getpixel((x,y))
            #print(pixel)
            # If the pixel is not black...
            if pixel != (0):
                # Check to see if we've created a sub-mask...
                pixel_str = str(pixel)
                sub_mask = sub_masks.get(pixel_str)
                if sub_mask is None:
                   # Create a sub-mask (one bit per pixel) and add to the dictionary
                    # Note: we add 1 pixel of padding in each direction
                    # because the contours module doesn't handle cases
                    # where pixels bleed to the edge of the image
                    sub_masks[pixel_str] = Image.new('1', (width+2, height+2))

                # Set the pixel value to 1 (default is 0), accounting for padding
                sub_masks[pixel_str].putpixel((x+1, y+1), 1)

    return sub_masks, width, height

In [3]:

def create_image(mask_image, filename1,width1, height1, image_id):
    image_det=                  {
                                     'licence':0,
                                     'filename':filename1 , 
                                     'width':width1 , 
                                     'height':height1,
                                     'id':image_id 
                                }       
                
    return image_det 


In [4]:
import os
from imutils import paths

basepath='./cervic_train/'
folderpath= basepath+'binary/'
folderpathorg = basepath+ 'original/'

# imagePaths = list(paths.list_images(folderpath))


class_names=[]
filenames1=[]
filenames=[]
mask_images=[]

for dirname in os.listdir(folderpath):
        class_names.append(dirname)
        path=folderpath+'/'+dirname+'/'
        for filename in os.listdir(path):
            img= Image.open(path+filename)
            mask_images.append(img)
            filenames1.append(dirname+'/'+filename)
            orgfilename=filename.replace('-d.bmp','.BMP')
            filenames.append(folderpathorg+dirname+'/'+orgfilename)
print(class_names)    
# print(filenames)  
# print(filenames1)

 

['normal_intermediate', 'light_dysplastic', 'moderate_dysplastic', 'severe_dysplastic', 'normal_columnar', 'carcinoma_in_situ', 'normal_superficiel']


In [5]:
# print(filenames1)
# print(filenames)
# print(mask_images)

In [6]:
print(filenames1[0].split('/')[0])

normal_intermediate


In [7]:
def category_find(class_name):

        switcher =    {
                        'normal_intermediate': 1,
                        'light_dysplastic': 2, 
                        'moderate_dysplastic':3,
                        'severe_dysplastic' :4 ,
                        'normal_columnar':5 ,
                        'carcinoma_in_situ':6,
                        'normal_superficiel':7 
             }
        return switcher.get(class_name)

In [8]:
#  category_id= category_find(filenames1[120].split('/')[0])

In [9]:
# print(category_id)

In [10]:

imgannotations = []
fileid=0



categ=[]
# Create the annotations
annotations = []
annotation_id = 1
image_id = 1
is_crowd = 0
fileid=0

     
for (mask_image, classname) in zip(mask_images, filenames1):
    #print('loop')
    classname1= classname.split('/')[0]
    #print(classname.split('/')[0])
    print(image_id)
    category_id1= category_find(classname1)
    category={'supercategory':'cervic', 'category_id': category_id1, 'name': classname.split('/')[0]}
    categ.append(category)
    imglist=[5,28,42,46,56,65,66,71,72,73,94,109,135,148,162,166,174,178,179,180,188,202,224,227,228,236,241,244,245,246,
             251,254,258,263,275,288,304,309,317,319,324,326,338,346,371,400,406,424,447,465,471,474,476,497,518,
              527,540,542,543,571,575,596,602,606,640]
         
    
    if image_id not in imglist :
        
        sub_masks, width, height = create_sub_masks(mask_image)
        for color, sub_mask in sub_masks.items():
            #category_id = category_ids[image_id][color]
            
            #category_id.append(cat_id)
            annot= create_image(sub_mask, filenames[fileid],width, height, image_id)
            imgannotations.append(annot)
            #width, height = mask_image.size
            annotation = create_sub_mask_annotation(sub_mask, image_id, category_id1, annotation_id, is_crowd )
            annotations.append(annotation)

            annotation_id = 1
   # elif image_id==16:
   #     continue
    image_id += 1
    fileid +=1
#print(json.dumps(annotations))

import json


# category_id = 2
# class_name= 'light_dysplastic'
image_info = {

                    'info': 
                              {
                                    "description": "cervic class 7 Dataset",
                                    "url": "http://cocodataset.org",
                                    "version": "1.0",
                                    "year": 2019,
                                    "contributor": "Trois Infotech",
                                    "date_created": "2019/12/27"
                               },
                    'licenses':  
                                 {
                                    "url": "http://creativecommons.org/licenses/by-nc-sa/2.0/",
                                    "id": 0,
                                    "name": "Attribution-NonCommercial-ShareAlike License"
                                 },
                    'categories':categ, 
                                
                    'images': imgannotations,
                    'annotations': annotations
                                  
}

with open('./cervic_train/cervic_all_class_train.json', 'w') as json_file:
 
        json.dump(image_info, json_file)
#         json.dump(annotations1, json_file)
#         json.dump(annotations, json_file)

1
[[270.5 129. ]
 [270.5 128. ]
 [270.5 127. ]
 ...
 [269.5 130. ]
 [270.  129.5]
 [270.5 129. ]]
POLYGON ((128 269.5, 127 269.5, 126 269.5, 125 269.5, 124 269.5, 123 269.5, 122 269.5, 121 269.5, 120 269.5, 119 269.5, 118 269.5, 117 269.5, 116 269.5, 115 269.5, 114 269.5, 113 269.5, 112 269.5, 111 269.5, 110.5 269, 110 268.5, 109 268.5, 108.5 268, 108 267.5, 107 267.5, 106.5 267, 106 266.5, 105.5 266, 105 265.5, 104.5 265, 104.5 264, 104 263.5, 103.5 263, 103.5 262, 103 261.5, 102.5 261, 102 260.5, 101.5 260, 101.5 259, 101.5 258, 101 257.5, 100.5 257, 100 256.5, 99.5 256, 99.5 255, 99.5 254, 99 253.5, 98.5 253, 98.5 252, 98 251.5, 97.5 251, 97 250.5, 96.5 250, 96 249.5, 95 249.5, 94.5 249, 94 248.5, 93 248.5, 92.5 248, 92 247.5, 91 247.5, 90.5 247, 90 246.5, 89.5 246, 89 245.5, 88 245.5, 87 245.5, 86 245.5, 85 245.5, 84 245.5, 83.5 245, 83 244.5, 82 244.5, 81.5 244, 81 243.5, 80.5 243, 80 242.5, 79.5 242, 79 241.5, 78.5 241, 78 240.5, 77.5 240, 77 239.5, 76.5 239, 76 238.5, 75.5 238, 

[[356.5 247. ]
 [356.5 246. ]
 [356.5 245. ]
 ...
 [355.5 248. ]
 [356.  247.5]
 [356.5 247. ]]
POLYGON ((246 355.5, 245 355.5, 244 355.5, 243 355.5, 242 355.5, 241 355.5, 240 355.5, 239 355.5, 238 355.5, 237 355.5, 236 355.5, 235 355.5, 234 355.5, 233 355.5, 232 355.5, 231 355.5, 230 355.5, 229 355.5, 228 355.5, 227 355.5, 226 355.5, 225 355.5, 224 355.5, 223 355.5, 222 355.5, 221 355.5, 220 355.5, 219 355.5, 218 355.5, 217 355.5, 216 355.5, 215 355.5, 214 355.5, 213 355.5, 212 355.5, 211.5 355, 211 354.5, 210 354.5, 209 354.5, 208 354.5, 207 354.5, 206 354.5, 205 354.5, 204 354.5, 203 354.5, 202 354.5, 201.5 354, 201 353.5, 200 353.5, 199.5 353, 199 352.5, 198 352.5, 197.5 352, 197 351.5, 196 351.5, 195 351.5, 194 351.5, 193 351.5, 192 351.5, 191 351.5, 190.5 351, 190 350.5, 189 350.5, 188 350.5, 187.5 350, 187 349.5, 186 349.5, 185.5 349, 185 348.5, 184 348.5, 183.5 348, 183 347.5, 182 347.5, 181 347.5, 180 347.5, 179.5 347, 179 346.5, 178 346.5, 177 346.5, 176 346.5, 175 346.5, 174

[[339.5 157. ]
 [339.5 156. ]
 [339.5 155. ]
 ...
 [338.5 158. ]
 [339.  157.5]
 [339.5 157. ]]
POLYGON ((156 338.5, 155 338.5, 154 338.5, 153 338.5, 152 338.5, 151 338.5, 150 338.5, 149 338.5, 148 338.5, 147 338.5, 146 338.5, 145 338.5, 144 338.5, 143.5 338, 143 337.5, 142 337.5, 141 337.5, 140.5 337, 140 336.5, 139 336.5, 138 336.5, 137 336.5, 136 336.5, 135.5 336, 135 335.5, 134 335.5, 133 335.5, 132 335.5, 131 335.5, 130 335.5, 129.5 335, 129 334.5, 128 334.5, 127 334.5, 126 334.5, 125 334.5, 124 334.5, 123 334.5, 122 334.5, 121 334.5, 120 334.5, 119 334.5, 118 334.5, 117 334.5, 116 334.5, 115 334.5, 114 334.5, 113.5 335, 113 335.5, 112 335.5, 111 335.5, 110 335.5, 109 335.5, 108 335.5, 107 335.5, 106 335.5, 105 335.5, 104.5 336, 104 336.5, 103 336.5, 102 336.5, 101 336.5, 100 336.5, 99 336.5, 98 336.5, 97 336.5, 96 336.5, 95 336.5, 94 336.5, 93 336.5, 92 336.5, 91 336.5, 90 336.5, 89 336.5, 88 336.5, 87 336.5, 86 336.5, 85 336.5, 84.5 336, 84 335.5, 83 335.5, 82.5 335, 82 334.5, 8

[[205.5 183. ]
 [205.5 182. ]
 [205.5 181. ]
 ...
 [204.5 184. ]
 [205.  183.5]
 [205.5 183. ]]
POLYGON ((182 204.5, 181 204.5, 180 204.5, 179 204.5, 178 204.5, 177 204.5, 176 204.5, 175 204.5, 174 204.5, 173 204.5, 172 204.5, 171 204.5, 170 204.5, 169 204.5, 168 204.5, 167 204.5, 166 204.5, 165 204.5, 164 204.5, 163 204.5, 162 204.5, 161 204.5, 160 204.5, 159 204.5, 158 204.5, 157 204.5, 156.5 204, 156 203.5, 155 203.5, 154 203.5, 153 203.5, 152 203.5, 151 203.5, 150 203.5, 149.5 203, 149 202.5, 148 202.5, 147 202.5, 146 202.5, 145 202.5, 144 202.5, 143 202.5, 142 202.5, 141 202.5, 140 202.5, 139 202.5, 138 202.5, 137.5 202, 137 201.5, 136 201.5, 135 201.5, 134 201.5, 133 201.5, 132 201.5, 131 201.5, 130.5 201, 130 200.5, 129 200.5, 128 200.5, 127 200.5, 126 200.5, 125 200.5, 124 200.5, 123 200.5, 122.5 200, 122 199.5, 121 199.5, 120 199.5, 119 199.5, 118 199.5, 117 199.5, 116 199.5, 115 199.5, 114 199.5, 113 199.5, 112 199.5, 111 199.5, 110 199.5, 109 199.5, 108 199.5, 107.5 199, 107

[[360.5 185. ]
 [360.5 184. ]
 [360.5 183. ]
 ...
 [359.5 186. ]
 [360.  185.5]
 [360.5 185. ]]
POLYGON ((184 359.5, 183 359.5, 182 359.5, 181 359.5, 180 359.5, 179 359.5, 178 359.5, 177 359.5, 176 359.5, 175 359.5, 174 359.5, 173 359.5, 172 359.5, 171 359.5, 170 359.5, 169 359.5, 168 359.5, 167 359.5, 166 359.5, 165 359.5, 164 359.5, 163 359.5, 162 359.5, 161 359.5, 160 359.5, 159 359.5, 158 359.5, 157 359.5, 156 359.5, 155 359.5, 154 359.5, 153 359.5, 152 359.5, 151 359.5, 150.5 359, 150 358.5, 149.5 358, 149 357.5, 148 357.5, 147 357.5, 146 357.5, 145 357.5, 144 357.5, 143 357.5, 142 357.5, 141 357.5, 140.5 357, 140 356.5, 139.5 356, 139 355.5, 138 355.5, 137 355.5, 136 355.5, 135.5 355, 135 354.5, 134 354.5, 133.5 354, 133 353.5, 132 353.5, 131 353.5, 130.5 353, 130 352.5, 129 352.5, 128.5 352, 128 351.5, 127.5 351, 127 350.5, 126.5 350, 126 349.5, 125.5 349, 125 348.5, 124.5 348, 124 347.5, 123 347.5, 122 347.5, 121.5 347, 121 346.5, 120.5 346, 120 345.5, 119.5 345, 119.5 344, 119

...

[[300.5 461. ]
 [300.5 460. ]
 [300.5 459. ]
 ...
 [299.5 462. ]
 [300.  461.5]
 [300.5 461. ]]
POLYGON ((460 299.5, 459 299.5, 458 299.5, 457 299.5, 456 299.5, 455 299.5, 454 299.5, 453 299.5, 452 299.5, 451 299.5, 450 299.5, 449 299.5, 448.5 299, 448 298.5, 447 298.5, 446 298.5, 445 298.5, 444 298.5, 443.5 298, 443 297.5, 442 297.5, 441 297.5, 440 297.5, 439 297.5, 438 297.5, 437 297.5, 436.5 297, 436 296.5, 435 296.5, 434 296.5, 433 296.5, 432.5 296, 432 295.5, 431 295.5, 430 295.5, 429 295.5, 428 295.5, 427.5 295, 427 294.5, 426 294.5, 425 294.5, 424 294.5, 423 294.5, 422 294.5, 421 294.5, 420 294.5, 419 294.5, 418 294.5, 417 294.5, 416 294.5, 415 294.5, 414 294.5, 413 294.5, 412 294.5, 411 294.5, 410 294.5, 409 294.5, 408 294.5, 407 294.5, 406 294.5, 405 294.5, 404.5 295, 404 295.5, 403 295.5, 402 295.5, 401 295.5, 400 295.5, 399 295.5, 398 295.5, 397 295.5, 396 295.5, 395.5 295, 395 294.5, 394 294.5, 393 294.5, 392 294.5, 391 294.5, 390.5 294, 390 293.5, 389 293.5, 388 293.5, 387

[[234.5 115. ]
 [234.5 114. ]
 [234.5 113. ]
 ...
 [233.5 116. ]
 [234.  115.5]
 [234.5 115. ]]
POLYGON ((114 233.5, 113 233.5, 112 233.5, 111 233.5, 110 233.5, 109 233.5, 108 233.5, 107 233.5, 106 233.5, 105 233.5, 104 233.5, 103 233.5, 102 233.5, 101.5 233, 101 232.5, 100 232.5, 99.5 232, 99 231.5, 98.5 231, 98 230.5, 97 230.5, 96.5 230, 96 229.5, 95.5 229, 95 228.5, 94.5 228, 94 227.5, 93 227.5, 92.5 227, 92 226.5, 91.5 226, 91 225.5, 90.5 225, 90 224.5, 89 224.5, 88.5 224, 88 223.5, 87.5 223, 87 222.5, 86 222.5, 85.5 222, 85 221.5, 84 221.5, 83.5 221, 83 220.5, 82 220.5, 81.5 220, 81 219.5, 80 219.5, 79 219.5, 78.5 219, 78 218.5, 77 218.5, 76.5 218, 76 217.5, 75 217.5, 74 217.5, 73.5 217, 73 216.5, 72 216.5, 71 216.5, 70.5 216, 70 215.5, 69 215.5, 68 215.5, 67.5 215, 67 214.5, 66 214.5, 65 214.5, 64.5 214, 64 213.5, 63 213.5, 62.5 213, 62 212.5, 61.5 212, 61 211.5, 60.5 211, 60 210.5, 59.5 210, 59 209.5, 58.5 209, 58 208.5, 57.5 208, 57 207.5, 56.5 207, 56 206.5, 55.5 206, 55 205.5

[[259.5 190. ]
 [259.  189.5]
 [258.5 189. ]
 ...
 [258.5 191. ]
 [259.  190.5]
 [259.5 190. ]]
POLYGON ((189 258.5, 188.5 258, 188 257.5, 187 257.5, 186 257.5, 185 257.5, 184.5 257, 184 256.5, 183 256.5, 182 256.5, 181 256.5, 180.5 256, 180 255.5, 179 255.5, 178 255.5, 177 255.5, 176 255.5, 175.5 255, 175 254.5, 174 254.5, 173 254.5, 172.5 254, 172 253.5, 171 253.5, 170 253.5, 169 253.5, 168 253.5, 167.5 253, 167 252.5, 166 252.5, 165 252.5, 164.5 252, 164 251.5, 163 251.5, 162.5 251, 162 250.5, 161 250.5, 160.5 250, 160 249.5, 159 249.5, 158 249.5, 157.5 249, 157 248.5, 156 248.5, 155.5 248, 155 247.5, 154 247.5, 153 247.5, 152.5 247, 152 246.5, 151 246.5, 150 246.5, 149 246.5, 148 246.5, 147 246.5, 146 246.5, 145.5 246, 145 245.5, 144 245.5, 143 245.5, 142 245.5, 141 245.5, 140.5 245, 140 244.5, 139 244.5, 138 244.5, 137 244.5, 136 244.5, 135 244.5, 134.5 244, 134 243.5, 133 243.5, 132 243.5, 131 243.5, 130 243.5, 129 243.5, 128 243.5, 127 243.5, 126 243.5, 125 243.5, 124 243.5, 123

[[284.5 236. ]
 [284.5 235. ]
 [284.5 234. ]
 ...
 [283.5 237. ]
 [284.  236.5]
 [284.5 236. ]]
POLYGON ((235 283.5, 234 283.5, 233 283.5, 232 283.5, 231 283.5, 230 283.5, 229 283.5, 228 283.5, 227 283.5, 226 283.5, 225 283.5, 224.5 283, 224 282.5, 223 282.5, 222 282.5, 221 282.5, 220.5 282, 220 281.5, 219 281.5, 218.5 281, 218 280.5, 217 280.5, 216.5 280, 216 279.5, 215 279.5, 214.5 279, 214 278.5, 213.5 278, 213 277.5, 212.5 277, 212 276.5, 211.5 276, 211 275.5, 210.5 275, 210 274.5, 209.5 274, 209 273.5, 208 273.5, 207 273.5, 206 273.5, 205 273.5, 204.5 273, 204 272.5, 203.5 272, 203 271.5, 202.5 271, 202 270.5, 201 270.5, 200.5 270, 200 269.5, 199 269.5, 198 269.5, 197.5 269, 197 268.5, 196 268.5, 195 268.5, 194.5 268, 194 267.5, 193 267.5, 192 267.5, 191.5 267, 191 266.5, 190.5 266, 190 265.5, 189 265.5, 188.5 265, 188 264.5, 187.5 264, 187 263.5, 186 263.5, 185 263.5, 184.5 263, 184 262.5, 183 262.5, 182.5 262, 182 261.5, 181 261.5, 180 261.5, 179.5 261, 179 260.5, 178 260.5, 177

[[242.5 273. ]
 [242.5 272. ]
 [242.5 271. ]
 ...
 [241.5 274. ]
 [242.  273.5]
 [242.5 273. ]]
POLYGON ((272 241.5, 271 241.5, 270 241.5, 269 241.5, 268 241.5, 267 241.5, 266 241.5, 265 241.5, 264 241.5, 263 241.5, 262 241.5, 261 241.5, 260 241.5, 259 241.5, 258 241.5, 257 241.5, 256 241.5, 255 241.5, 254 241.5, 253 241.5, 252 241.5, 251 241.5, 250 241.5, 249 241.5, 248 241.5, 247 241.5, 246 241.5, 245 241.5, 244.5 241, 244 240.5, 243 240.5, 242 240.5, 241 240.5, 240 240.5, 239.5 240, 239 239.5, 238 239.5, 237 239.5, 236 239.5, 235.5 239, 235 238.5, 234 238.5, 233 238.5, 232 238.5, 231 238.5, 230 238.5, 229 238.5, 228.5 238, 228 237.5, 227 237.5, 226 237.5, 225 237.5, 224 237.5, 223 237.5, 222 237.5, 221 237.5, 220 237.5, 219 237.5, 218 237.5, 217 237.5, 216 237.5, 215 237.5, 214 237.5, 213 237.5, 212 237.5, 211 237.5, 210 237.5, 209 237.5, 208 237.5, 207 237.5, 206 237.5, 205 237.5, 204.5 237, 204 236.5, 203 236.5, 202 236.5, 201 236.5, 200 236.5, 199 236.5, 198 236.5, 197 236.5, 196

In [110]:
import IPython
import os
import json
import random
import numpy as np
import requests
from io import BytesIO
from math import trunc
from PIL import Image as PILImage
from PIL import ImageDraw as PILImageDraw

In [114]:
# Load the dataset json
class CocoDataset():
    def __init__(self, annotation_path, image_dir):
        self.annotation_path = annotation_path
        self.image_dir = image_dir
        self.colors = colors = ['blue','red','gold','green','purple',   'orange', 'salmon', 'pink', 
                                'orchid', 'slateblue', 'limegreen', 'seagreen', 'darkgreen', 'olive',
                               'teal', 'aquamarine', 'steelblue', 'powderblue', 'dodgerblue', 'navy',
                               'magenta', 'sienna', 'maroon']
        
        json_file = open(self.annotation_path)
        self.coco = json.load(json_file)
        json_file.close()
        
        self.process_info()
        self.process_licenses()
        self.process_categories()
        self.process_images()
        self.process_segmentations()
            
        
    def display_info(self):
        print('Dataset Info:')
        print('=============')
        for key, item in self.info.items():
            print('  {}: {}'.format(key, item))
        
        requirements = [['description', str],
                        ['url', str],
                        ['version', str],
                        ['year', int],
                        ['contributor', str],
                        ['date_created', str]]
        for req, req_type in requirements:
            if req not in self.info:
                print('ERROR: {} is missing'.format(req))
            elif type(self.info[req]) != req_type:
                print('ERROR: {} should be type {}'.format(req, str(req_type)))
        print('')

        
    def display_licenses(self):
        print('Licenses:')
        print('=========')
        
        requirements = [['id', int],
                        ['url', str],
                         ['name', str]]
        for license in self.licenses:
#             for key, item in license.items():
#                 print('  {}: {}'.format(key, item))
            for req, req_type in requirements:
                if req not in license:
                    print('ERROR: {} is missing'.format(req))
                elif type(license[req]) != req_type:
                    print('ERROR: {} should be type {}'.format(req, str(req_type)))
            print('')
        print('')
        
    def display_categories(self):
        print('Categories:')
        print('=========')
        for sc_key, sc_val in self.super_categories.items():
            print('  super_category: {}'.format(sc_key))
            for cat_id in sc_val:
                print('    id {}: {}'.format(cat_id, self.categories[cat_id]['name']))
            print('')
    
    def display_image(self, image_id, show_polys=True, show_bbox=True, show_crowds=True, use_url=False):
        print('Image:')
        print('======')
        if image_id == 'random':
            image_id = random.choice(list(self.images.keys()))
        
        # Print the image info
        image = self.images[image_id]
        for key, val in image.items():
            print('  {}: {}'.format(key, val))
            
        # Open the image
        if use_url:
            image_path = image['coco_url']
            response = requests.get(image_path)
            image = PILImage.open(BytesIO(response.content))
            
        else:
#             image_path = os.path.join(self.image_dir, image['filename'])
            image_path= image['filename']
            image = PILImage.open(image_path)
        
        # Calculate the size and adjusted display size
        max_width = 600
        image_width, image_height = image.size
        adjusted_width = min(image_width, max_width)
        adjusted_ratio = adjusted_width / image_width
        adjusted_height = adjusted_ratio * image_height
        
        # Create list of polygons to be drawn
        polygons = {}
        bbox_polygons = {}
        rle_regions = {}
        poly_colors = {}
        print('  segmentations ({}):'.format(len(self.segmentations[image_id])))
        for i, segm in enumerate(self.segmentations[image_id]):
            polygons_list = []
            if segm['iscrowd'] != 0:
                # Gotta decode the RLE
                px = 0
                x, y = 0, 0
                rle_list = []
                for j, counts in enumerate(segm['segmentation']['counts']):
                    if j % 2 == 0:
                        # Empty pixels
                        px += counts
                    else:
                        # Need to draw on these pixels, since we are drawing in vector form,
                        # we need to draw horizontal lines on the image
                        x_start = trunc(trunc(px / image_height) * adjusted_ratio)
                        y_start = trunc(px % image_height * adjusted_ratio)
                        px += counts
                        x_end = trunc(trunc(px / image_height) * adjusted_ratio)
                        y_end = trunc(px % image_height * adjusted_ratio)
                        if x_end == x_start:
                            # This is only on one line
                            rle_list.append({'x': x_start, 'y': y_start, 'width': 1 , 'height': (y_end - y_start)})
                        if x_end > x_start:
                            # This spans more than one line
                            # Insert top line first
                            rle_list.append({'x': x_start, 'y': y_start, 'width': 1, 'height': (image_height - y_start)})
                            
                            # Insert middle lines if needed
                            lines_spanned = x_end - x_start + 1 # total number of lines spanned
                            full_lines_to_insert = lines_spanned - 2
                            if full_lines_to_insert > 0:
                                full_lines_to_insert = trunc(full_lines_to_insert * adjusted_ratio)
                                rle_list.append({'x': (x_start + 1), 'y': 0, 'width': full_lines_to_insert, 'height': image_height})
                                
                            # Insert bottom line
                            rle_list.append({'x': x_end, 'y': 0, 'width': 1, 'height': y_end})
                if len(rle_list) > 0:
                    rle_regions[segm['id']] = rle_list  
            else:
                # Add the polygon segmentation
                for segmentation_points in segm['segmentation']:
                    segmentation_points = np.multiply(segmentation_points, adjusted_ratio).astype(int)
                    polygons_list.append(str(segmentation_points).lstrip('[').rstrip(']'))
            polygons[segm['image_id']] = polygons_list
            if i < len(self.colors):
                poly_colors[segm['image_id']] = self.colors[i]
            else:
                poly_colors[segm['image_id']] = 'white'
            
            bbox = segm['bbox']
            bbox_points = [bbox[0], bbox[1], bbox[0] + bbox[2], bbox[1],
                           bbox[0] + bbox[2], bbox[1] + bbox[3], bbox[0], bbox[1] + bbox[3],
                           bbox[0], bbox[1]]
            bbox_points = np.multiply(bbox_points, adjusted_ratio).astype(int)
            bbox_polygons[segm['image_id']] = str(bbox_points).lstrip('[').rstrip(']')
            
            # Print details
            print('    {}:{}:{}'.format(segm['image_id'], poly_colors[segm['image_id']], self.categories[segm['category_id']]))
        
        
        
        # Draw segmentation polygons on image
        html  = '<div class="container" style="position:relative;">'
        html += '<img src="{}" style="position:relative;top:0px;left:0px;width:{}px;">'.format(image_path, adjusted_width)
        html += '<div class="svgclass"><svg width="{}" height="{}">'.format(adjusted_width, adjusted_height)
        
        if show_polys:
            for seg_id, points_list in polygons.items():
                fill_color = poly_colors[seg_id]
                stroke_color = poly_colors[seg_id]
                for points in points_list:
                    html += '<polygon points="{}" style="fill:{}; stroke:{}; stroke-width:1; fill-opacity:0.5" />'.format(points, fill_color, stroke_color)
        
        if show_crowds:
            for seg_id, rect_list in rle_regions.items():
                fill_color = poly_colors[seg_id]
                stroke_color = poly_colors[seg_id]
                for rect_def in rect_list:
                    x, y = rect_def['x'], rect_def['y']
                    w, h = rect_def['width'], rect_def['height']
                    html += '<rect x="{}" y="{}" width="{}" height="{}" style="fill:{}; stroke:{}; stroke-width:1; fill-opacity:0.5; stroke-opacity:0.5" />'.format(x, y, w, h, fill_color, stroke_color)
            
        if show_bbox:
            for seg_id, points in bbox_polygons.items():
                fill_color = poly_colors[seg_id]
                stroke_color = poly_colors[seg_id]
                html += '<polygon points="{}" style="fill:{}; stroke:{}; stroke-width:1; fill-opacity:0" />'.format(points, fill_color, stroke_color)
                
        html += '</svg></div>'
        html += '</div>'
        html += '<style>'
        html += '.svgclass { position:absolute; top:0px; left:0px;}'
        html += '</style>'
        return html
       
    def process_info(self):
        self.info = self.coco['info']
    
    def process_licenses(self):
        self.licenses = self.coco['licenses']
    
    def process_categories(self):
        self.categories = {}
        self.super_categories = {}
        for category in self.coco['categories']:
            cat_id = category['category_id']
            #cat_id = 1
            super_category = category['supercategory']
            #super_category = 1
            # Add category to the categories dict
            if cat_id not in self.categories:
                self.categories[cat_id] = category
            else:
                print("ERROR: Skipping duplicate category id: {}".format(category))

            # Add category to super_categories dict
            if super_category not in self.super_categories:
                self.super_categories[super_category] = {cat_id} # Create a new set with the category id
            else:
                self.super_categories[super_category] |= {cat_id} # Add category id to the set
                
    def process_images(self):
        self.images = {}
        for image in self.coco['images']:
            image_id = image['id']
            if image_id in self.images:
                print("ERROR: Skipping duplicate image id: {}".format(image))
            else:
                self.images[image_id] = image
                
    def process_segmentations(self):
        self.segmentations = {}
        for segmentation in self.coco['annotations']:
            image_id = segmentation['image_id']
            if image_id not in self.segmentations:
                self.segmentations[image_id] = []
            self.segmentations[image_id].append(segmentation)

In [121]:
annotation_path = './cervic_train/cervic_all_class_train.json'
image_dir = './cervic_train/original/carcino_in_situ'

coco_dataset = CocoDataset(annotation_path, image_dir)
coco_dataset.display_info()
# coco_dataset.display_licenses()
coco_dataset.display_categories()

ERROR: Skipping duplicate category id: {'supercategory': 'cervic', 'category_id': 1, 'name': 'normal_intermediate'}
ERROR: Skipping duplicate category id: {'supercategory': 'cervic', 'category_id': 1, 'name': 'normal_intermediate'}
ERROR: Skipping duplicate category id: {'supercategory': 'cervic', 'category_id': 1, 'name': 'normal_intermediate'}
ERROR: Skipping duplicate category id: {'supercategory': 'cervic', 'category_id': 1, 'name': 'normal_intermediate'}
ERROR: Skipping duplicate category id: {'supercategory': 'cervic', 'category_id': 1, 'name': 'normal_intermediate'}
ERROR: Skipping duplicate category id: {'supercategory': 'cervic', 'category_id': 1, 'name': 'normal_intermediate'}
ERROR: Skipping duplicate category id: {'supercategory': 'cervic', 'category_id': 1, 'name': 'normal_intermediate'}
ERROR: Skipping duplicate category id: {'supercategory': 'cervic', 'category_id': 1, 'name': 'normal_intermediate'}
ERROR: Skipping duplicate category id: {'supercategory': 'cervic', 'cate

In [127]:

html = coco_dataset.display_image(250, use_url=False)
IPython.display.HTML(html)

Image:
  licence: 0
  filename: ./cervic_train/original/moderate_dysplastic/149098972-149099015-002.BMP
  width: 121
  height: 168
  id: 250
  segmentations (1):
    250:blue:{'supercategory': 'cervic', 'category_id': 3, 'name': 'moderate_dysplastic'}


In [124]:
html = coco_dataset.display_image(600, use_url=False)
IPython.display.HTML(html)

Image:
  licence: 0
  filename: ./cervic_train/original/normal_superficiel/157183964-157183991-001.BMP
  width: 254
  height: 132
  id: 600
  segmentations (1):
    600:blue:{'supercategory': 'cervic', 'category_id': 7, 'name': 'normal_superficiel'}


In [125]:
annotation_path='./cervic_train/cervic_all_class_train.json'
with open(annotation_path) as json_file:
    lines = json_file.readlines()
for line in lines:
    print(line)

{"info": {"description": "cervic class 7 Dataset", "url": "http://cocodataset.org", "version": "1.0", "year": 2019, "contributor": "Trois Infotech", "date_created": "2019/12/27"}, "licenses": {"url": "http://creativecommons.org/licenses/by-nc-sa/2.0/", "id": 0, "name": "Attribution-NonCommercial-ShareAlike License"}, "categories": [{"supercategory": "cervic", "category_id": 1, "name": "normal_intermediate"}, {"supercategory": "cervic", "category_id": 1, "name": "normal_intermediate"}, {"supercategory": "cervic", "category_id": 1, "name": "normal_intermediate"}, {"supercategory": "cervic", "category_id": 1, "name": "normal_intermediate"}, {"supercategory": "cervic", "category_id": 1, "name": "normal_intermediate"}, {"supercategory": "cervic", "category_id": 1, "name": "normal_intermediate"}, {"supercategory": "cervic", "category_id": 1, "name": "normal_intermediate"}, {"supercategory": "cervic", "category_id": 1, "name": "normal_intermediate"}, {"supercategory": "cervic", "category_id":